In [ ]:
import exploration.option_trades as rvol
import datetime
import pandas as pd

from exploration.curve_trades import on_the_run
from scipy.interpolate import interp1d
from matplotlib import pyplot as plt
from ipywidgets import widgets

In [ ]:
w = widgets.Dropdown(
    options=['IG', 'HY'],
    value='IG',
    description='Index:',
    disabled=False,
)
w

In [ ]:
index = w.value
start_date=datetime.date(2014, 6, 11)
onTR, model = rvol.realized_vol(index, on_the_run('IG'), "5yr", years=3)

In [ ]:
#onTR.plot()

In [ ]:
model.summary()

In [ ]:
#compute lo and hi percentiles of atm volatility daily change (vol of vol)
rvol.vol_var()

In [ ]:
df = rvol.atm_vol(index, start_date, moneyness = .2)
df['steepness'] = df.otm_vol - df.atm_vol
df1 = df.reset_index()
df1['date'] = df1.quotedate.dt.date
df1 = df1.groupby(['date','expiry']).last()
#Need to do: the vol looks jumpy, is it because of quote source issue? yes, need to first try to get the same quote source...

In [ ]:
r = []
time = [1/12, 2/12, 3/12, 4/12, 5/12]
for t in time:
    for date, g in df1.groupby(level='date'):
        f = interp1d(g['T'].values, g['steepness'].values, fill_value='extrapolate')
        r.append((date, t, f(t)))
steepness = pd.DataFrame(r, columns=['date', 'T', 'steepness'])
steepness = steepness.set_index(['date','T']).unstack().astype('float')
steepness.columns = steepness.columns.droplevel()
steepness.ewm(span = 3).mean().plot()

In [ ]:
(steepness.iloc[-1] - steepness.mean()) / steepness.std()

In [ ]:
#Need to do: look at steepness not on moneyness but on delta range (60 delta vs 20 delta)